In [1]:
import requests
from selenium import webdriver
from bs4 import BeautifulSoup
from fake_useragent import UserAgent
import pandas as pd
import numpy as np
from tqdm import tqdm_notebook
from multiprocessing import Pool, cpu_count
from concurrent.futures import ThreadPoolExecutor
UserAgent().chrome

'Mozilla/5.0 (Windows NT 6.4; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/41.0.2225.0 Safari/537.36'

# Настройки

## Ссылка на обкачивание сайта

In [2]:
# array_split = np.array_split(np.arange(4000), 12)

In [5]:
# %%time
# link = "https://sbermarket.ru/stores/"
# data = requests.request("GET", link)
# URLS = set()
# for i in tqdm_notebook(range(4000)):
#     response = requests.get(link + str(i), headers={'User-Agent': UserAgent().chrome})
#     url = response.url
#     length = len(url.split('?')[-1])
#     url = url[:-length-1]
#     if 'stores' in url:
#         continue
#     URLS = URLS.union(set([url]))

In [6]:
# markets = pd.DataFrame(URLS, columns=['shops'])[1:].reset_index(drop=True)

In [2]:
markets = pd.read_csv('shops.csv')

In [7]:
names  = []
for shop in markets['shops']:
    names.append(shop.split('/')[-1])
markets['name'] = names
markets.to_csv('shops.csv', index=False)

In [8]:
html = data.text
soup = BeautifulSoup(html,'html.parser') 
objects = soup.find_all(lambda tag: tag.get('class') == ['store_selector_2jWME'])

NameError: name 'data' is not defined

In [3]:
links = []
for obj in objects:
    new_link = 'https://sbermarket.ru' + obj['href']
    links.append(new_link)

NameError: name 'objects' is not defined

In [15]:
links

[]

In [10]:
shops = {'Метро': 'https://sbermarket.ru/metro',
'Ашан':'https://sbermarket.ru/auchan',
'Лента':'https://sbermarket.ru/lenta',
'BILLA': 'https://sbermarket.ru/billa',
'ВкусВилл': 'https://sbermarket.ru/vkusvill',
'Азбука вкуса': 'https://sbermarket.ru/azbukavkusa',
'Азбука вкуса быстрая доставка': 'https://sbermarket.ru/azbukavkusa_sd',
'Селгрос': 'https://sbermarket.ru/selgros',
'Okey': 'https://sbermarket.ru/okey'}

# Функции для поиска ссылок и скачивания данных с сайтов.

In [4]:
def download_link(page_link):
    try:
        response = requests.get(page_link, headers={'User-Agent': UserAgent().chrome})
        html = response.text
        return html
    except:
        return ''

def find_links(html):
    if html == '':
        return []
    soup = BeautifulSoup(html,'html.parser') 
    objects = soup.find_all(lambda tag: tag.name == 'a' and tag.get('class') == ['taxon-title__link'])
    links = []
    for obj in objects:
        new_link = 'https://sbermarket.ru' + obj['href']
        links.append(new_link)
    return links

# Реализация метода поиска в ширину для поиска всех ссылок

In [10]:

# links = 
# Поиск в ширину - ПВШ (Breadth First Search - BFS)
def bfs(link):
    if link in visited:  # Если вершина уже посещена, выходим
        return
    visited.add(link)  # Посетили вершину v
    BFS.append(link)  # Запоминаем порядок обхода
    # print("v = %d" % v)
    html = download_link(link)
    new_links_list =  find_links(html)
    for i in new_links_list:  # Все смежные с v вершины
        if not i in visited:
            Q.append(i)
    while Q:
        bfs(Q.pop(0))

In [11]:
visited = set()  # Посещена ли вершина?
Q = []  # Очередь
BFS = []

# Поиск ссылок по всем магазинам

In [12]:
%%time
df = pd.DataFrame()
for ind, row in tqdm_notebook(markets.iterrows(), total=markets.shape[0]):
    visited = set()  # Посещена ли вершина?
    Q = []  # Очередь
    BFS = []
    bfs(row['shops'])
    result = pd.DataFrame(BFS, columns=['links'])
    result['магазин'] = row['name']
    df = pd.concat([df, result])
    df.drop_duplicates()

C:\Users\buthy\anaconda3\lib\site-packages\ipykernel_launcher.py:2: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



Wall time: 4h 56min 12s


In [13]:
links = df.copy()

In [14]:
def download_html(links, driver):
    
    df = pd.DataFrame()
    for link in tqdm_notebook(links):
        driver.get(link)
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        html = driver.page_source
        df_new = parse_html_to_df(html) 
        df_new['link'] = link
        df = pd.concat([df, df_new])
        df.drop_duplicates()
    return df

def parse_html_to_df(html):
    soup = BeautifulSoup(html,'html.parser') 
    prices_to_parse = soup.find_all(lambda tag: tag.name == 'div' and tag.get('class') == ['product__price'])
    prices = [obj.text.strip() for obj in prices_to_parse]
    title_to_parse = soup.find_all(lambda tag: tag.name == 'p' and tag.get('class') == ['product__title'])
    titles = [obj.text for obj in title_to_parse]
    volum_to_parse = soup.find_all(lambda tag: tag.name == 'p' and tag.get('class') == ['product__volume'])
    volums = [obj.text.strip() for obj in volum_to_parse]
    return pd.DataFrame(np.array([titles, prices, volums]).T, columns=['название', 'цена', 'объем'])

In [15]:
# links = all_links.copy()

In [16]:
links_to_del = set()
for link in links['links']:
    length = len(link.split('/')[-1])
    link_del = link[:-length-1]
    links_to_del = links_to_del | set([link_del])

In [17]:
links.head()

links магазин
0                       https://sbermarket.ru/market  market
1  https://sbermarket.ru/market/tolko-dlia-podpis...  market
2  https://sbermarket.ru/market/dieshievlie-chiem...  market
3     https://sbermarket.ru/market/ovoshchi-i-frukty  market
4     https://sbermarket.ru/market/voda-soki-napitki  market

In [18]:
links = links[~links['links'].isin(links_to_del)].reset_index(drop=True)

In [10]:
links_split = np.array_split(links['links'].values, 12)

In [23]:
links.to_csv('fresh_links.csv', index=False)

In [6]:
links = pd.read_csv('fresh_links.csv')

In [11]:
def update_df(links):
    driver = webdriver.Edge(executable_path=r'C:\Users\buthy\Downloads\edgedriver_win321\msedgedriver.exe')
    driver.set_script_timeout(600)
    df = download_html(links, driver)
    driver.quit();
    return df

In [12]:
links_split[10][501]

'https://sbermarket.ru/titan/bytovaia-khimiia/sriedstva-dlia-mytia-posudy/dlia-posudomoiechnykh-mashin'

In [9]:
driver = webdriver.Edge(executable_path=r'C:\Users\buthy\Downloads\edgedriver_win321\msedgedriver.exe')
driver.set_script_timeout(600)
df = download_html([links_split[10][502]], driver)

SessionNotCreatedException: Message: session not created: This version of MSEdgeDriver only supports MSEdge version 87
Current browser version is 89.0.774.57 with binary path C:\Program Files (x86)\Microsoft\Edge\Application\msedge.exe


In [13]:
with ThreadPoolExecutor(4) as executor:
    results = executor.map(update_df, links_split)

In [30]:
# df = pd.DataFrame()
for df_new in results:
    try:
        df = pd.concat([df, df_new])
        df.drop_duplicates()
    except:
        continue

In [49]:
df_to_check = df_all[df_all['название'].isna()].reset_index(drop=True)
links_split = np.array_split(df_to_check ['link'].values, 12)

In [51]:
with ThreadPoolExecutor(12) as executor:
    results = executor.map(update_df, links_split)

C:\Users\buthy\anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


In [46]:
df.to_csv('temp_results.csv', index=False)

In [47]:
df_all.to_csv('temp_results_with_nan.csv', index=False)

In [52]:
for df_new in results:
    df = pd.concat([df, df_new])
    df.drop_duplicates()
    

In [43]:
df_to_check['магазин'].value_counts()

lenta                 1318
komandor               512
alleya                 497
titan                  463
bistronom              423
karavan                415
samberi                404
parus                  394
zelenoeyabloko         312
agrokompleks           296
7stolitsa              287
vega                   276
kit                    274
TDHOROSHIJ             273
horoshij               248
azbukavkusa_sd         140
tvoydom                121
yves-rocher             35
vkusvill                27
auchansm                24
auchan                  19
provino                 14
deya                    10
metrodlyaofica          10
parfumlider              7
metro                    6
okey                     6
sigma                    3
idea                     3
bahetle                  2
5lb                      2
ulibkaradugi             2
atoll                    2
kirovski                 2
osen                     1
imperial                 1
fissman                  1
s

In [42]:
df_all.shape

(149655, 5)

In [59]:
df_all.drop_duplicates()

название      цена    объем  \
0              Жевательная резинка Orbit White Bubblemint   31,99 ₽  10 драж   
1       Мицеллярная вода Garnier очищающее средство дл...  279,99 ₽   400 мл   
2       Шампунь для волос Garnier Fructis SOS Восстано...  204,99 ₽   400 мл   
3        Чай черный Лисма Крепкий в пакетиках 2 г х 25 шт   42,99 ₽     50 г   
4       Шампунь для волос Garnier Fructis Рост во всю ...  204,99 ₽   400 мл   
...                                                   ...       ...      ...   
214913  Зубная щетка BioMed Black с древесным углем ср...   99,00 ₽     1 шт   
214914  Ополаскиватель для полости рта BioMed Super wh...  195,00 ₽    0,5 л   
214915  Ополаскиватель BioMed Sensitive для полости рт...  195,00 ₽     1 шт   
214916  Жидкое мыло Чистая Линия Для всей семьи березо...  135,00 ₽    533 г   
214917  Жидкое мыло BioMio Bio-Soap с маслом абрикоса ...  185,00 ₽    300 г   

                                                     link магазин  
0       https://sbermarket.ru/market/tolko-dlia-podpis...  market  
1       https://sbermarket.ru/market/tolko-dlia-podpis...  market  
2       https://sbermarket.ru/market/tolko-dlia-podpis...  market  
3       https://sbermarket.ru/market/tolko-dlia-podpis...  market  
4       https://sbermarket.ru/market/tolko-dlia-podpis...  market  
...                                                   ...     ...  
214913  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...     NaN  
214914  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...     NaN  
214915  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...     NaN  
214916  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...     NaN  
214917  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...     NaN  

[214154 rows x 5 columns]

In [63]:
df_all

название      цена    объем  \
0              Жевательная резинка Orbit White Bubblemint   31,99 ₽  10 драж   
1       Мицеллярная вода Garnier очищающее средство дл...  279,99 ₽   400 мл   
2       Шампунь для волос Garnier Fructis SOS Восстано...  204,99 ₽   400 мл   
3        Чай черный Лисма Крепкий в пакетиках 2 г х 25 шт   42,99 ₽     50 г   
4       Шампунь для волос Garnier Fructis Рост во всю ...  204,99 ₽   400 мл   
...                                                   ...       ...      ...   
214913  Зубная щетка BioMed Black с древесным углем ср...   99,00 ₽     1 шт   
214914  Ополаскиватель для полости рта BioMed Super wh...  195,00 ₽    0,5 л   
214915  Ополаскиватель BioMed Sensitive для полости рт...  195,00 ₽     1 шт   
214916  Жидкое мыло Чистая Линия Для всей семьи березо...  135,00 ₽    533 г   
214917  Жидкое мыло BioMio Bio-Soap с маслом абрикоса ...  185,00 ₽    300 г   

                                                     link     магазин  
0       https://sbermarket.ru/market/tolko-dlia-podpis...      market  
1       https://sbermarket.ru/market/tolko-dlia-podpis...      market  
2       https://sbermarket.ru/market/tolko-dlia-podpis...      market  
3       https://sbermarket.ru/market/tolko-dlia-podpis...      market  
4       https://sbermarket.ru/market/tolko-dlia-podpis...      market  
...                                                   ...         ...  
214913  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...  TDHOROSHIJ  
214914  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...  TDHOROSHIJ  
214915  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...  TDHOROSHIJ  
214916  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...  TDHOROSHIJ  
214917  https://sbermarket.ru/TDHOROSHIJ/zozh/naturaln...  TDHOROSHIJ  

[214918 rows x 5 columns]

In [58]:
df_all.shape

(214918, 5)

In [32]:
links.rename(columns={'links':'link'}, inplace=True)

In [62]:
df_all = df.drop(columns='магазин').merge(links, how='left')

In [64]:
df_all.to_excel('shops_25_02_21.xlsx', index=False)

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/spar/dietskiie-tovary/ighry-i-ighrushki/aktivnyie-ighry' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/spar/dietskiie-tovary/khobbi-i-tvorchiestvo/risovaniie' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/spar/dietskiie-tovary/khobbi-i-tvorchiestvo/liepka' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/spar/diet

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/megas/ryba-i-morieprodukty/morieprodukty/krievietki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/megas/ryba-i-morieprodukty/morieprodukty/midii' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/megas/ryba-i-morieprodukty/morieprodukty/morskiie-vodorosli' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/megas/ryba-i

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/azbukavkusa/katalogh-av/fiermierskiie-produkty' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/azbukavkusa/katalogh-av/zakazatielnyie-dni/bakalieia' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/azbukavkusa/katalogh-av/zakazatielnyie-dni/khlieb-vypiechka' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/azbukavkusa

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/razvitiie-i-obuchieniie/knighi/entsiklopiedii' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/razvitiie-i-obuchieniie/knighi/dietskaia-khudozhiestviennaia-litieratura' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/razvitiie-i-obuchieniie/knighi/skazki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\s

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/zakazatielnyie-dni' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/kosmietika-i-ghighiiena' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/dlia-doma-i-dachi' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/ovoshchi-i-frukty/ovoshchi' since it exceeds Excel's limit of 65,530 URLS per 

...

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/idea/sladosti/marmielad-ziefir-pastila/marmielad' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/idea/sladosti/marmielad-ziefir-pastila/ziefir' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/idea/sladosti/marmielad-ziefir-pastila/pastila' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/idea/sladosti/marmielad-ziefi

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/shan/bytovaia-khimiia/chistiashchiie-i-moiushchiie-sriedstva/sriedstva-dlia-prochistki-trub' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/shan/bytovaia-khimiia/chistiashchiie-i-moiushchiie-sriedstva/univiersalnyie-sriedstva' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/shan/bytovaia-khimiia/osviezhitieli-vozdukha/aerozolnyie' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\wor

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/konsiervy-i-solienia/konsiervirovannyie-ovoshchi/assorti' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/konsiervy-i-solienia/konsiervirovannyie-ovoshchi/zielien' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/konsiervy-i-solienia/konsiervirovannyie-ovoshchi/adzhika' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https:/

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/tvoydom/katalogh-tvoidom/riemont-i-instrumient/lakokrasochnyie-matierialy/rastvoritieli' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/tvoydom/katalogh-tvoidom/riemont-i-instrumient/lakokrasochnyie-matierialy/emali' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/tvoydom/katalogh-tvoidom/riemont-i-instrumient/maliarnyi-instrumient-i-matierialy/abrazivnyie-matierialy' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anac

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [32]:
%%time
df_new = pd.DataFrame()
for ind, row in tqdm_notebook(markets[:6].iterrows(), total=markets.shape[0]):
    visited = set()  # Посещена ли вершина?
    Q = []  # Очередь
    BFS = []
    bfs(row['shops'])
    result = pd.DataFrame(BFS, columns=['links'])
    result['магазин'] = row['name']
    df_new = pd.concat([df_new, result])
    df_new.drop_duplicates()

C:\Users\buthy\anaconda3\lib\site-packages\ipykernel_launcher.py:2: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



Wall time: 37min 17s


In [33]:
new_links = df_new.copy()

In [34]:
links_to_del = set()
for link in new_links['links']:
    length = len(link.split('/')[-1])
    link_del = link[:-length-1]
    links_to_del = links_to_del | set([link_del])

In [35]:
new_links.head()

links магазин
0                    https://sbermarket.ru/market  market
1  https://sbermarket.ru/market/ovoshchi-i-frukty  market
2  https://sbermarket.ru/market/voda-soki-napitki  market
3      https://sbermarket.ru/market/moloko-iaitsa  market
4          https://sbermarket.ru/market/bakalieia  market

In [36]:
new_links = new_links[~new_links['links'].isin(links_to_del)].reset_index(drop=True)

In [37]:
links_split = np.array_split(new_links['links'].values, 12)

In [38]:
def update_df(links):
    driver = webdriver.Edge(executable_path=r'C:\Users\buthy\Downloads\edgedriver_win321\msedgedriver.exe')
    driver.set_script_timeout(600)
    df = download_html(links, driver)
    driver.quit();
    return df

In [39]:
with ThreadPoolExecutor(12) as executor:
    results = executor.map(update_df, links_split)

C:\Users\buthy\anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


KeyboardInterrupt: 

In [40]:
df_update = pd.DataFrame()
for df_2 in results:
    df_update = pd.concat([df_update, df_2])
    df_update.drop_duplicates()

In [47]:
df_update = df_update.merge(new_links.rename(columns={'links':'link'}), how='left')

In [45]:
# df_update.drop(columns='магазин', inplace=True)

In [ ]:
df_update.to_excel('shops_08_02_21_2.xlsx', index=False)

In [42]:
df.head()

название  \
0             Хлебцы Щедрые Бородинские тонкие 170 г   
1  Хлебцы Dr. Korner кукурузно-рисовые с прованск...   
2                    Хлебцы Щедрые ржаные с чесноком   
3                               Хлебцы Щедрые Ржаные   
4        Круассаны 7 Days Мини c кремом ваниль 300 г   

                                         цена  объем  \
0                                     63,99 ₽  170 г   
1                                     80,99 ₽  100 г   
2                                     34,99 ₽  100 г   
3                                     55,99 ₽  200 г   
4  88,00 ₽\n107,90 ₽\n\n\n\n-18%\n\n\nдо 8.02  300 г   

                                            link магазин  
0  https://sbermarket.ru/deya/khlieb-i-vypiechka    deya  
1  https://sbermarket.ru/deya/khlieb-i-vypiechka    deya  
2  https://sbermarket.ru/deya/khlieb-i-vypiechka    deya  
3  https://sbermarket.ru/deya/khlieb-i-vypiechka    deya  
4  https://sbermarket.ru/deya/khlieb-i-vypiechka    deya

In [53]:
df_all_new = pd.concat([df, df_update])
df_all_new = df_all_new.drop_duplicates()

In [55]:
df_all_new.to_excel('all_shops_08_02_21.xlsx', index=False)

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/okey/sportivnyie-tovary/vsie-dlia-rybalki/rybolovnyie-iashchiki-kontieiniery' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/okey/sportivnyie-tovary/vodnyie-vidy-sporta/naduvnyie-matrasy-krughi-ighrushki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/okey/sportivnyie-tovary/vielosport-samokaty-skieity-roliki/vieloaksiessuary' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksh

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/ighrushki/kukly-i-koliaski/kukly-barbi' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/ighrushki/kukly-i-koliaski/pupsy' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/dochkisinochki/ds-dietskiie-tovary/ighrushki/siuzhietno-rolievyie-ighry/blastiery-g-blast' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksh

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/bakalieia/gorokh-fasol-chiechievitsa' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/bakalieia/makarony-pasta-viermishiel' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/bakalieia/sakhar-i-zamienitieli' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/fresh25/bakalieia/sol' since it exceeds E

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/metro/vsie-dlia-riemonta/kriepiezh/montazhnaia-piena' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/metro/vsie-dlia-riemonta/kriepiezh/montazhnyie-lienty' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/metro/vsie-dlia-riemonta/lakokrasochnyie-matierialy-diekor/rastvoritieli-ochistitieli' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL '

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/victoria/zozh/zdorovaia-diieta/granola' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/victoria/zozh/zdorovaia-diieta/miusli-khlopia-otrubi' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/victoria/zozh/zdorovaia-diieta/miaso-ptitsa' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/victoria/ryba-i-morieprodukty/ryba-

...

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/moloko-iaitsa/kislomolochnyie-produkty' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/moloko-iaitsa/smietana-zapravki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/moloko-iaitsa/maioniez' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/vega/moloko-iaitsa/morozhienoie' since it exceeds Excel's limi

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/parus/ryba-i-morieprodukty/ikra/zakuska' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/parus/ryba-i-morieprodukty/polufabrikaty-iz-ryby/rybnyie-kotliety' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/parus/ryba-i-morieprodukty/polufabrikaty-iz-ryby/rybnyie-palochki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/samberi/vsie-dlia-riemonta/ruchnyie-instrumienty/maliarnyi-instrumient' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/samberi/vsie-dlia-riemonta/ruchnyie-instrumienty/otviertki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/samberi/vsie-dlia-riemonta/ruchnyie-instrumienty/nozhi-nozhnitsy-shilia-liezviia-stiekloriezy' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:9

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/alleya/zozh/zdorovaia-diieta/miusli-khlopia-otrubi' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/alleya/zozh/zdorovaia-diieta/napitki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/alleya/zozh/zdorovaia-diieta/miaso-ptitsa' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/alleya/ryba-i-morieprodukty/ryba-okhlazhd

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/auchansm/dietskiie-tovary/ighry-i-ighrushki/miaghkiie-ighrushki' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: UserWarning: Ignoring URL 'https://sbermarket.ru/auchansm/dietskiie-tovary/ighry-i-ighrushki/ighrovyie-nabory' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  "65,530 URLS per worksheet." % force_unicode(url))
C:\Users\buthy\anaconda3\lib\site-packages\xlsxwriter\worksheet.py:945: Use

# Лента

In [8]:
%%time
visited = set()  # Посещена ли вершина?
Q = []  # Очередь
BFS = []
html = download_link(page_link)
links = find_links(html)
bfs('https://sbermarket.ru/lenta')

Wall time: 23min 4s


In [9]:
import pandas as pd
df_lenta = pd.DataFrame(BFS, columns=['links'])
df_lenta['магазин'] = 'Лента'
df_lenta.to_csv('links_lenta.csv', index=False)

# Азбука вкуса

In [12]:
%%time
visited = set()  # Посещена ли вершина?
Q = []  # Очередь
BFS = []
html = download_link(page_link)
links = find_links(html)
bfs('https://sbermarket.ru/azbukavkusa_sd')

Wall time: 1min 51s


In [13]:
import pandas as pd
df_azbuka = pd.DataFrame(BFS, columns=['links'])
df_azbuka['магазин'] = 'Лента'
df_azbuka.to_csv('links_azbuka.csv', index=False)